# Определение стоимости автомобилей

Сервис по продаже автомобилей с пробегом  разрабатывает приложение для привлечения новых клиентов. В нём можно быстро узнать рыночную стоимость своего автомобиля. На основе исторические данные необходимо построить модель для определения стоимости автомобиля.

Необходимо:
- Импортировать данные
- Провести обзорный анализ EDA
- Подготовить данные к расчету модели (пропуски, выбросы, дубли, некорректные значения и пр)
- Выделить данные для обучения и валидации
- Построить и обучить несколько моделей
- Выбрать лучшую модель
- Сделать общий вывод

In [1]:
! pip install pandas-profiling[notebook]
! pip install lightgbm
! pip install optuna

In [69]:
import pandas as pd
import numpy as np
import lightgbm as lgb
import optuna

from pandas_profiling import ProfileReport

from sklearn.linear_model import LinearRegression
from sklearn.model_selection import cross_val_score, train_test_split
from sklearn.ensemble import RandomForestRegressor
from sklearn.svm import SVR
from sklearn.metrics import mean_squared_error
from sklearn.preprocessing import OrdinalEncoder

## Подготовка данных

### Импорт

In [72]:
df = pd.read_csv('/datasets/autos.csv')
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 354369 entries, 0 to 354368
Data columns (total 16 columns):
 #   Column             Non-Null Count   Dtype 
---  ------             --------------   ----- 
 0   DateCrawled        354369 non-null  object
 1   Price              354369 non-null  int64 
 2   VehicleType        316879 non-null  object
 3   RegistrationYear   354369 non-null  int64 
 4   Gearbox            334536 non-null  object
 5   Power              354369 non-null  int64 
 6   Model              334664 non-null  object
 7   Kilometer          354369 non-null  int64 
 8   RegistrationMonth  354369 non-null  int64 
 9   FuelType           321474 non-null  object
 10  Brand              354369 non-null  object
 11  NotRepaired        283215 non-null  object
 12  DateCreated        354369 non-null  object
 13  NumberOfPictures   354369 non-null  int64 
 14  PostalCode         354369 non-null  int64 
 15  LastSeen           354369 non-null  object
dtypes: int64(7), object(

Признаки
- DateCrawled — дата скачивания анкеты из базы
- VehicleType — тип автомобильного кузова
- RegistrationYear — год регистрации автомобиля
- Gearbox — тип коробки передач
- Power — мощность (л. с.)
- Model — модель автомобиля
- Kilometer — пробег (км)
- RegistrationMonth — месяц регистрации автомобиля
- FuelType — тип топлива
- Brand — марка автомобиля
- NotRepaired — была машина в ремонте или нет
- DateCreated — дата создания анкеты
- NumberOfPictures — количество фотографий автомобиля
- PostalCode — почтовый индекс владельца анкеты (пользователя)
- LastSeen — дата последней активности пользователя

Целевой признак
- Price — цена (евро)

### EDA

In [73]:
ProfileReport(df)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [104]:
# Проверяем корректность данных года регистрации
print(df['RegistrationYear'].unique())
print('Количество некорректных записей года регисттрации', len(df.query('RegistrationYear > 2022 or RegistrationYear < 1900')))

[1993 2011 2004 2001 2008 1995 1980 2014 1998 2005 1910 2016 2007 2009
 2002 2018 1997 1990 2017 1981 2003 1994 1991 1984 2006 1999 2012 2010
 2000 1992 2013 1996 1985 1989 2015 1982 1976 1983 1973 1111 1969 1971
 1987 1986 1988 1970 1965 1945 1925 1974 1979 1955 1978 1972 1968 1977
 1961 1960 1966 1975 1963 1964 5000 1954 1958 1967 1959 9999 1956 3200
 1000 1941 8888 1500 2200 4100 1962 1929 1957 1940 3000 2066 1949 2019
 1937 1951 1800 1953 1234 8000 5300 9000 2900 6000 5900 5911 1933 1400
 1950 4000 1948 1952 1200 8500 1932 1255 3700 3800 4800 1942 7000 1935
 1936 6500 1923 2290 2500 1930 1001 9450 1944 1943 1934 1938 1688 2800
 1253 1928 1919 5555 5600 1600 2222 1039 9996 1300 8455 1931 1915 4500
 1920 1602 7800 9229 1947 1927 7100 8200 1946 7500 3500]
Количество некорректных записей года регисттрации 171


In [105]:
# Проверяем корректность данных создания анкеты
print(df['RegistrationYear'].unique())
print('Количество некорректных записей года регистрации', len(df.query('RegistrationYear > 2022 or RegistrationYear < 1900')))

[1993 2011 2004 2001 2008 1995 1980 2014 1998 2005 1910 2016 2007 2009
 2002 2018 1997 1990 2017 1981 2003 1994 1991 1984 2006 1999 2012 2010
 2000 1992 2013 1996 1985 1989 2015 1982 1976 1983 1973 1111 1969 1971
 1987 1986 1988 1970 1965 1945 1925 1974 1979 1955 1978 1972 1968 1977
 1961 1960 1966 1975 1963 1964 5000 1954 1958 1967 1959 9999 1956 3200
 1000 1941 8888 1500 2200 4100 1962 1929 1957 1940 3000 2066 1949 2019
 1937 1951 1800 1953 1234 8000 5300 9000 2900 6000 5900 5911 1933 1400
 1950 4000 1948 1952 1200 8500 1932 1255 3700 3800 4800 1942 7000 1935
 1936 6500 1923 2290 2500 1930 1001 9450 1944 1943 1934 1938 1688 2800
 1253 1928 1919 5555 5600 1600 2222 1039 9996 1300 8455 1931 1915 4500
 1920 1602 7800 9229 1947 1927 7100 8200 1946 7500 3500]
Количество некорректных записей года регистрации 171


**Резюме**:
- VehicleType - Тип кузова 
10.6% процентов пропусков, применить частотный преобразователь

- Gearbox - Тип коробки
5.6% пропуска, применить частотный преобразователь

- Model - Модель
5.6% пропуска. Заполнить Unknown

- RegistrationMonth - Месяц регистраии автомобиля
10.5% заполнено нулями, применить частотный преобразователь

- FuelType - Тип топлива
9.3% пропуска, применить частотный преобразователь

- NotRepaired - Была машина в ремонте или нет
20.1% пропуска, применить частотный преобразователь

- Price - Цена
3.0% заполнено нулями, удалить.

- Power - Мощность л.с
11.4% заполнено нулями, применить частотный преобразователь

- Преобразовать к дате:  
    - DateCreated
    - LastSeen
    - DateCrawled
    
    
- Дубликаты:  
Выявлено 4 явных дубликата. Их удаляем  



- Есть ошибки в данных года регистрации  
Ошибочных записей не много, можно удалить их
    
    
- Корреляция:
    - Умеренная положительная корреляция цены и мощности - чем мощнее машина, тем дороже (логично)
    - Умеренная положительная корреляция года регистрации и цены - чем новее машина, тем дороже (логично)
    - Слабая отрицательная корреляция пробега и цены - чем больше пробег, тем дешевле (логично)

### Удаление дубликатов

In [106]:
print('Записей до удаления', df.shape[0])
df = df.drop_duplicates()
print('Записей после удаления', df.shape[0])

Записей до удаления 354365
Записей после удаления 354365


### Обработка пропусков, типов данных и нулей

In [107]:
# Преобразуем типы 
df['DateCreated'] = pd.pandas.to_datetime(df['DateCreated'])
df['LastSeen'] = pd.pandas.to_datetime(df['LastSeen'])
df['DateCrawled'] = pd.pandas.to_datetime(df['DateCrawled'])

In [108]:
# Обрабатываем нули месяца регистрации 
df.loc[df['RegistrationMonth'] == 0, 'RegistrationMonth'] = None
df[df['RegistrationMonth'].isnull()].shape

(37352, 16)

In [109]:
# Обрабатываем нули мощности
df.loc[df['Power'] == 0, 'Power'] = None
df[df['Power'].isnull()].shape

(40225, 16)

In [110]:
# Частотное преобразование пропусков
transform_columns = ['VehicleType', 'Gearbox','FuelType', 'NotRepaired', 'RegistrationMonth', 'Power']
transform = {}
transform_index = {}

for col in transform_columns:
    X = []
    arr = df[col].value_counts(normalize = True)
    for idx, x in enumerate(arr.values):
        if idx == 0:
            X.append((0, x))
        else:
            X.append((X[idx-1][1], X[idx-1][1] + x))
    transform[col] = X
    transform_index[col] = list(arr.index)

# Функция частотного заполнения пропуска
def frequency_conversion(column):
    X = transform[column]
    rnd = np.random.random()
    for idx, x in enumerate(X):
        if rnd <= x[1] and rnd >= x[0]:
            return transform_index[column][idx]


# Обрабатываем пропуски
for col in transform_columns:
    df.loc[df[col].isnull(), col] = df[df[col].isnull()][col].apply(lambda v: frequency_conversion(col)) 
    
df[transform_columns].info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 354365 entries, 0 to 354368
Data columns (total 6 columns):
 #   Column             Non-Null Count   Dtype  
---  ------             --------------   -----  
 0   VehicleType        354365 non-null  object 
 1   Gearbox            354365 non-null  object 
 2   FuelType           354365 non-null  object 
 3   NotRepaired        354365 non-null  object 
 4   RegistrationMonth  354365 non-null  float64
 5   Power              354365 non-null  float64
dtypes: float64(2), object(4)
memory usage: 18.9+ MB


In [111]:
# Заполнение пустых моделей
df['Model'] = df['Model'].fillna('unknown')
df['Model'].isnull().sum()

0

In [112]:
# Удаление записей с нулевыми ценами
df = df.query('Price > 0')
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 343593 entries, 0 to 354368
Data columns (total 16 columns):
 #   Column             Non-Null Count   Dtype         
---  ------             --------------   -----         
 0   DateCrawled        343593 non-null  datetime64[ns]
 1   Price              343593 non-null  int64         
 2   VehicleType        343593 non-null  object        
 3   RegistrationYear   343593 non-null  int64         
 4   Gearbox            343593 non-null  object        
 5   Power              343593 non-null  float64       
 6   Model              343593 non-null  object        
 7   Kilometer          343593 non-null  int64         
 8   RegistrationMonth  343593 non-null  float64       
 9   FuelType           343593 non-null  object        
 10  Brand              343593 non-null  object        
 11  NotRepaired        343593 non-null  object        
 12  DateCreated        343593 non-null  datetime64[ns]
 13  NumberOfPictures   343593 non-null  int64   

In [113]:
# Удаление записей с некорректным годом регистрации
df = df.query('RegistrationYear <= 2022 or RegistrationYear > 1900')
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 343593 entries, 0 to 354368
Data columns (total 16 columns):
 #   Column             Non-Null Count   Dtype         
---  ------             --------------   -----         
 0   DateCrawled        343593 non-null  datetime64[ns]
 1   Price              343593 non-null  int64         
 2   VehicleType        343593 non-null  object        
 3   RegistrationYear   343593 non-null  int64         
 4   Gearbox            343593 non-null  object        
 5   Power              343593 non-null  float64       
 6   Model              343593 non-null  object        
 7   Kilometer          343593 non-null  int64         
 8   RegistrationMonth  343593 non-null  float64       
 9   FuelType           343593 non-null  object        
 10  Brand              343593 non-null  object        
 11  NotRepaired        343593 non-null  object        
 12  DateCreated        343593 non-null  datetime64[ns]
 13  NumberOfPictures   343593 non-null  int64   

In [114]:
# Удаляем признаки, которые не влияют на модель
df = df.drop(columns=['DateCrawled', 'DateCreated', 'LastSeen', 'PostalCode', 'NumberOfPictures'])


In [115]:
# Кодирование категориальных признаков OHE
df_ohe = pd.get_dummies(df, drop_first = True)
list(df_ohe.columns)

['Price',
 'RegistrationYear',
 'Power',
 'Kilometer',
 'RegistrationMonth',
 'VehicleType_convertible',
 'VehicleType_coupe',
 'VehicleType_other',
 'VehicleType_sedan',
 'VehicleType_small',
 'VehicleType_suv',
 'VehicleType_wagon',
 'Gearbox_manual',
 'Model_145',
 'Model_147',
 'Model_156',
 'Model_159',
 'Model_1_reihe',
 'Model_1er',
 'Model_200',
 'Model_2_reihe',
 'Model_300c',
 'Model_3_reihe',
 'Model_3er',
 'Model_4_reihe',
 'Model_500',
 'Model_5_reihe',
 'Model_5er',
 'Model_601',
 'Model_6_reihe',
 'Model_6er',
 'Model_7er',
 'Model_80',
 'Model_850',
 'Model_90',
 'Model_900',
 'Model_9000',
 'Model_911',
 'Model_a1',
 'Model_a2',
 'Model_a3',
 'Model_a4',
 'Model_a5',
 'Model_a6',
 'Model_a8',
 'Model_a_klasse',
 'Model_accord',
 'Model_agila',
 'Model_alhambra',
 'Model_almera',
 'Model_altea',
 'Model_amarok',
 'Model_antara',
 'Model_arosa',
 'Model_astra',
 'Model_auris',
 'Model_avensis',
 'Model_aveo',
 'Model_aygo',
 'Model_b_klasse',
 'Model_b_max',
 'Model_beet

In [117]:
# Порядковое кодирование категорий
obj_feat = list(df.loc[:, df.dtypes == 'object'].columns.values)

encoder = OrdinalEncoder()
encoder.fit(df[obj_feat])

df_ordinal = df.copy()
df_ordinal[obj_feat] = encoder.transform(df[obj_feat])

df_ordinal.head()

Price  VehicleType  RegistrationYear  Gearbox  Power  Model  Kilometer  \
0    480          4.0              1993      1.0   90.0  116.0     150000   
1  18300          2.0              2011      1.0  190.0  228.0     125000   
2   9800          6.0              2004      0.0  163.0  117.0     125000   
3   1500          5.0              2001      1.0   75.0  116.0     150000   
4   3600          5.0              2008      1.0   69.0  101.0      90000   

   RegistrationMonth  FuelType  Brand  NotRepaired  
0                4.0       6.0   38.0          0.0  
1                5.0       2.0    1.0          1.0  
2                8.0       2.0   14.0          0.0  
3                6.0       6.0   38.0          0.0  
4                7.0       2.0   31.0          0.0

## Обучение моделей

Задача моделирования относится к классу задач линейной регрессии

### Модель линейной регрессии

In [16]:
features = df_ohe.drop(['Price'], axis=1)
target = df_ohe['Price']

In [17]:
# Выделяем данные для обучения, валидации и тестирования
features_train, features_test, target_train, target_test = train_test_split(
    features, target, test_size=0.20, random_state=12345)

features_train, features_valid, target_train, target_valid = train_test_split(
    features_train, target_train, test_size=0.25, random_state=12345)

features_train_valid = pd.concat([features_train, features_valid])
target_train_valid = pd.concat([target_train, target_valid])

print('Записей обучающей выборки:', features_train.shape[0])
print('Записей валидационной выборки:', features_valid.shape[0])
print('Записей тестовой выборки:', features_test.shape[0])
print('Записей полной обучающей выборки (без валидации):', features_train_valid.shape[0])

Записей обучающей выборки: 206155
Записей валидационной выборки: 68719
Записей тестовой выборки: 68719
Записей полной обучающей выборки (без валидации): 274874


In [18]:
%%time

model_lr = LinearRegression()
model_lr.fit(features_train_valid, target_train_valid) 

Wall time: 4.88 s


LinearRegression()

In [19]:
%%time
predictions_test = model_lr.predict(features_test) 
result = mean_squared_error(target_test, predictions_test, squared= False)
print('Оценка качества модели:', result)

Оценка качества модели: 3224.4023380242434
Wall time: 158 ms


In [20]:
%%time

model_lr = LinearRegression()
scores =  cross_val_score(model_lr, features, target, scoring='neg_root_mean_squared_error', cv=5, verbose=True, n_jobs = -1)
print('Средняя оценка качества модели:', scores.mean())
print('Стандартное отклонение оценки:', scores.std())

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=-1)]: Done   5 out of   5 | elapsed:   19.5s finished


Средняя оценка качества модели: -3234.6636685027215
Стандартное отклонение оценки: 20.45877046457984
Wall time: 19.9 s


### Модель случайного леса регрессии

In [61]:
features = df_ordinal.drop(['Price'], axis=1)
target = df_ordinal['Price']

In [62]:
# Выделяем данные для обучения, валидации и тестирования
features_train, features_test, target_train, target_test = train_test_split(
    features, target, test_size=0.20, random_state=12345)

features_train, features_valid, target_train, target_valid = train_test_split(
    features_train, target_train, test_size=0.25, random_state=12345)

features_train_valid = pd.concat([features_train, features_valid])
target_train_valid = pd.concat([target_train, target_valid])

print('Записей обучающей выборки:', features_train.shape[0])
print('Записей валидационной выборки:', features_valid.shape[0])
print('Записей тестовой выборки:', features_test.shape[0])
print('Записей полной обучающей выборки (без валидации):', features_train_valid.shape[0])

Записей обучающей выборки: 206155
Записей валидационной выборки: 68719
Записей тестовой выборки: 68719
Записей полной обучающей выборки (без валидации): 274874


In [63]:
%%time

model_rfr = RandomForestRegressor(random_state=12345, n_jobs = -1, verbose=True)
model_rfr.fit(features_train_valid, target_train_valid) 

[Parallel(n_jobs=-1)]: Using backend ThreadingBackend with 4 concurrent workers.
[Parallel(n_jobs=-1)]: Done  42 tasks      | elapsed:   13.0s


Wall time: 31.6 s


[Parallel(n_jobs=-1)]: Done 100 out of 100 | elapsed:   31.4s finished


RandomForestRegressor(n_jobs=-1, random_state=12345, verbose=True)

In [64]:
%%time
predictions_test = model_rfr.predict(features_test) 
result = mean_squared_error(target_test, predictions_test, squared= False) 
print('Оценка качества модели:', result)

[Parallel(n_jobs=4)]: Using backend ThreadingBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:    0.4s


Оценка качества модели: 1757.4680594459237
Wall time: 1.28 s


[Parallel(n_jobs=4)]: Done 100 out of 100 | elapsed:    1.2s finished


In [65]:
%%time

model_rfr = RandomForestRegressor(random_state=12345, n_jobs = -1, verbose=True)
scores =  cross_val_score(model_rfr, features, target, scoring='neg_root_mean_squared_error', cv=5, verbose=True, n_jobs = -1)
print('Средняя оценка качества модели:', scores.mean())
print('Стандартное отклонение оценки:', scores.std())

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 4 concurrent workers.


Средняя оценка качества модели: -1768.429502773
Стандартное отклонение оценки: 5.009580287920816
Wall time: 2min 47s


[Parallel(n_jobs=-1)]: Done   5 out of   5 | elapsed:  2.8min finished


In [118]:
%%time

# Подбор гиперпараметров случайного леса
def objective(trial):
    #criterion = trial.suggest_categorical('criterion', ['mse', 'mae'])
    #bootstrap = trial.suggest_categorical('bootstrap',['True','False'])
    max_depth = trial.suggest_int('max_depth', 1, 20)
    #max_features = trial.suggest_categorical('max_features', ['auto', 'sqrt','log2'])
   # max_leaf_nodes = trial.suggest_int('max_leaf_nodes', 1, 10000)
    n_estimators =  trial.suggest_int('n_estimators', 30, 150)
    
    regr = RandomForestRegressor(
        #bootstrap = bootstrap, criterion = criterion,
        max_depth = max_depth, 
        #max_features = max_features,
        #max_leaf_nodes = max_leaf_nodes,
        n_estimators = n_estimators,
        n_jobs=-1)

    score = cross_val_score(regr, features_train_valid, target_train_valid, cv=5, scoring="neg_root_mean_squared_error")
    score_mean = score.mean()

    return score_mean

study = optuna.create_study(direction='maximize')
study.optimize(objective, n_trials=10)

print('Оптимальные параметры:', study.best_params)

optimised_rf = RandomForestRegressor(
    #bootstrap = study.best_params['bootstrap'], 
    #criterion = study.best_params['criterion'],
    max_depth = study.best_params['max_depth'], 
    #max_features = study.best_params['max_features'],
    #max_leaf_nodes = study.best_params['max_leaf_nodes'],
    n_estimators = study.best_params['n_estimators'],
    n_jobs=-1)

optimised_rf.fit(features_train_valid ,target_train_valid)

[I 2022-05-16 16:12:54,782] A new study created in memory with name: no-name-4f6fcb31-9a36-47e9-a40b-72d020dc51da
[I 2022-05-16 16:13:28,658] Trial 0 finished with value: -2735.1022616353025 and parameters: {'max_depth': 4, 'n_estimators': 106}. Best is trial 0 with value: -2735.1022616353025.
[I 2022-05-16 16:13:58,380] Trial 1 finished with value: -2734.9556986360817 and parameters: {'max_depth': 4, 'n_estimators': 103}. Best is trial 1 with value: -2734.9556986360817.
[I 2022-05-16 16:15:57,179] Trial 2 finished with value: -1868.848315196124 and parameters: {'max_depth': 14, 'n_estimators': 148}. Best is trial 2 with value: -1868.848315196124.
[I 2022-05-16 16:17:34,510] Trial 3 finished with value: -1909.006718302476 and parameters: {'max_depth': 13, 'n_estimators': 128}. Best is trial 2 with value: -1868.848315196124.
[I 2022-05-16 16:18:57,093] Trial 4 finished with value: -1787.9424565983547 and parameters: {'max_depth': 20, 'n_estimators': 77}. Best is trial 4 with value: -178

Оптимальные параметры: {'max_depth': 19, 'n_estimators': 90}
Wall time: 10min 57s


RandomForestRegressor(max_depth=19, n_estimators=90, n_jobs=-1)

In [119]:
%%time
predictions_test = optimised_rf.predict(features_test) 
result = mean_squared_error(target_test, predictions_test, squared= False) 
print('Оценка качества модели:', result)

Оценка качества модели: 1748.3194761464356
Wall time: 787 ms


### LightGBM

In [46]:
# Изменяем тип категориальных фич
obj_feat = list(df.loc[:, df.dtypes == 'object'].columns.values)
for feature in obj_feat:
    df[feature] = pd.Series(df[feature], dtype="category")

In [47]:
features = df.drop(['Price'], axis=1)
target = df['Price']

In [48]:
%%time

train_dataset = lgb.Dataset(features_train, target_train, feature_name=features_train.columns.tolist())
valid_dataset = lgb.Dataset(features_valid, target_valid, feature_name=features_train.columns.tolist())

booster = lgb.train({"objective": "regression"},
                    train_set=train_dataset, valid_sets=(valid_dataset,),
                    num_boost_round=10)


[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.006712 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 684
[LightGBM] [Info] Number of data points in the train set: 206155, number of used features: 10
[LightGBM] [Info] Start training from score 1355.891446
[1]	valid_0's l2: 780803
[2]	valid_0's l2: 684389
[3]	valid_0's l2: 604590
[4]	valid_0's l2: 539491
[5]	valid_0's l2: 485532
[6]	valid_0's l2: 442153
[7]	valid_0's l2: 405329
[8]	valid_0's l2: 373901
[9]	valid_0's l2: 347800
[10]	valid_0's l2: 325934
Wall time: 365 ms


In [49]:
%%time

predictions_test = booster.predict(features_test) 
result = mean_squared_error(target_test, predictions_test, squared= False)
print('Оценка качества модели:', result)

Оценка качества модели: 573.116315688478
Wall time: 35 ms


## Анализ моделей

- Проведен анализ применимости моделей линейной регрессии, случайного леса и LightGBM
- Результаты:  
| Модель      | Время обучения | Время предсказания | Качество |
| ----------- | -----------    |----------- |-----------    |
| Линейная регрессия      | 4.8 сек      |  0.158 сек    |3224|
| Случайный лес   | 31.6 сек        |  1.28 сек    |1757       |
| LightGBM   | 0.365 сек        |    0.035 сек   |573       |
- Самый худший результат качества показала модель линейной регрессии.
- Самый лучший результат качества и скорости - модель LightGBM. 
- Кросс-валидация практически не влияет на результат качества